In [1]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py


SRP_name = 'aggregates'
resolution = '1kbp_raw' 
species= 'mouse'


def calc_auroc (df_trial,predicted_score='predicted_score'):
    df_trial = df_trial.sort_values(by=[predicted_score], ascending=False)
    rank_abs = lambda x: stats.rankdata(x)
    predicts2 = np.apply_along_axis(rank_abs, 0, df_trial[predicted_score].values)
    df_trial['p'] = [y if x==1 else 0 for x,y in zip(df_trial['true_pos'], predicts2)]
    #print (df_trial['p'].sum())
    if df_trial['true_neg'].sum() == 0 or df_trial['true_pos'].sum() == 0:
        return np.nan
    else:
        return (((df_trial['p'].sum() /df_trial['true_pos'].sum() )- (df_trial['true_pos'].sum() + 1)/2)) / df_trial['true_neg'].sum()


exp_file_path=f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/spr/hic_gene_corr_inter_excluding_intra_chrom_pairs_hicexp.h5'
jac_sim_spr = hm.hiCMatrix(exp_file_path)
all_genes_spr = [x[3].decode() for x in jac_sim_spr.cut_intervals]
df_jac_corr = pd.DataFrame(jac_sim_spr.matrix.toarray() ,  index=all_genes_spr, columns = all_genes_spr)
  

input_path=f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/'
bins_bed = pd.read_csv(f'{input_path}/all_bins.bed', names=['chr', 'start', 'end', 'bin_id'])
bins_bed['bin_id'] = bins_bed.index
  
chr_list = bins_bed.drop_duplicates(subset=['chr'])['chr'].tolist()
chrom_index_list = {}
for chrom in chr_list:
      st = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[0]
      en = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[-1]
      chrom_index_list[chrom] = list(range(st, en+1))
gene_bed = pd.read_csv(f'{input_path}/all_gene.bed', names=['chr', 'start_bin', 'end_bin', 'gene'])



marker_list = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_cluster_markers.csv')

all_markers_df = []
for marker_type in ['class', 'subclass', 'cluster']:
	marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_type}_markers.csv')
	all_markers_df.append(marker_list)

marker_list = pd.concat(all_markers_df)
marker_list = marker_list.drop_duplicates(subset=['gene'])
df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/mouse_geneid_symbol.txt',sep='\t', names=['gene_id', 'gene'])
#df_ensg_name['gene'] = df_ensg_name['gene'].str.upper()
marker_list = marker_list.merge(df_ensg_name.drop_duplicates(subset=['gene']), right_on='gene', left_on='gene') 
#df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
#marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
#marker_list = marker_list.drop_duplicates(subset=['Ensembl_gene_identifier'])
marker_list = marker_list.drop_duplicates(subset=['gene_id'])



with h5py.File(f'{input_path}/hic_gene_gw_none_by_allbins_none.h5', 'r') as hf:
        tot_g = (list(hf.keys()))

all_background_markers = list(set(all_genes_spr) -  set(marker_list['gene_id'].tolist())) + marker_list['gene_id'].tolist()
all_background_markers = marker_list['gene_id'].tolist()
#all_background_markers = marker_list['cell_type'] != Non-Neuronal['gene_id'].tolist()

marker_contacts_list_inter = []

gene_list = []
with h5py.File(f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/hic_gene_gw_none_by_allbins_none.h5', 'r') as hf:
                   
                   for key in all_background_markers:
                    if key in tot_g:
                            gene_list.append(key)
                            gene_chrom = gene_bed[gene_bed['gene'] == key]['chr'].values[0]
                            #which ever chrom the gene falls into, those bins should be nan
                            my_data = hf[key][()]
                            my_data = my_data.astype('float32')
                            my_data[chrom_index_list[gene_chrom]] = np.nan
                            marker_contacts_list_inter.append(my_data)
                            
                            
my_data = np.array(marker_contacts_list_inter)

df_max_gene_inter_by_bins = pd.DataFrame(my_data, index=gene_list, columns = bins_bed['bin_id'].tolist())

df_max_gene_inter_by_bins_normalized = df_max_gene_inter_by_bins.div(df_max_gene_inter_by_bins.mean(axis=1, skipna=True), axis=0)
df_max_gene_inter_by_bins = df_max_gene_inter_by_bins_normalized

df_max_gene_inter_by_bins_sum = df_max_gene_inter_by_bins.sum().reset_index()

df_max_gene_inter_by_bins_sum_mean = df_max_gene_inter_by_bins.mean().reset_index()

INFO:numexpr.utils:Note: detected 192 virtual cores but NumExpr set to maximum of 64, check "NUMEXPR_MAX_THREADS" environment variable.
INFO:numexpr.utils:Note: NumExpr detected 192 cores but "NUMEXPR_MAX_THREADS" not set, so enforcing safe limit of 8.
INFO:numexpr.utils:NumExpr defaulting to 8 threads.
/grid/gillis/home/lohia/.conda/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (15,16) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


MemoryError: Unable to allocate 101. GiB for an array with shape (11023, 2462755) and data type float32

In [ ]:
marker_contacts_list_intra = []

gene_list = []
with h5py.File(f'/grid/gillis/data/lohia/hi_c_data_processing/data_human/{SRP_name}/{resolution}/max/hic_gene_gw_none_by_allbins_none.h5', 'r') as hf:
                   
                   for key in marker_list['Ensembl_gene_identifier'].tolist():
                    if key in all_genes_spr:
                            gene_list.append(key)
                            #which ever chrom the gene falls into, those bins should be nan
                            my_data = hf[key][()]
                            my_data = my_data.astype('float32')
                            gene_chrom = gene_bed[gene_bed['gene'] == key]['chr'].values[0]
                            my_data[chrom_index_list_intra[gene_chrom]] = np.nan
                            marker_contacts_list_intra.append(my_data)
                            

In [3]:
my_data = np.array(marker_contacts_list_inter)

In [37]:

chrom_index_list_intra = {}
for chrom in chr_list:
    index_list = []
    for chrom2 in chr_list:
        if chrom2 != chrom:
            index_list.extend(chrom_index_list[chrom2])
        
    
    chrom_index_list_intra[chrom] = index_list


In [43]:
number_of_genes_list = [1000]
marker_level_list = ['class']
#number_of_genes_list = [ 1000, 'opt', 10, 200]
#marker_level_list = ['class', 'subclass', 'cluster']
for number_of_genes in number_of_genes_list:
    for marker_level in marker_level_list:
        
        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/mouse_geneid_symbol.txt',sep='\t', names=['gene_id', 'gene'])
        #df_ensg_name['gene'] = df_ensg_name['gene'].str.upper()
        marker_list = marker_list.merge(df_ensg_name.drop_duplicates(subset=['gene']), right_on='gene', left_on='gene') 

        #marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/{species}/{marker_level}_markers_top1000.csv.gz', skiprows=1)
        #df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
        #marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
        marker_list = marker_list[marker_list['gene_id'].isin(tot_g)]
        

In [46]:
marker_list[marker_list['cell_type']!='Non-Neuronal']

group      cell_type  rank      gene  recurrence     auroc  fold_change  \
0      all      GABAergic     1      Gad1           7  0.941159   116.960472   
1      all      GABAergic     2      Gad2           7  0.928440   139.811415   
2      all      GABAergic     3     Erbb4           7  0.921449    81.717383   
3      all      GABAergic     4    Kcnip1           7  0.916919    32.252038   
4      all      GABAergic     5     Rbms3           7  0.902093    17.038869   
...    ...            ...   ...       ...         ...       ...          ...   
2088   all  Glutamatergic   996     Pcdh7           0  0.673757     1.461875   
2089   all  Glutamatergic   997     Asap2           0  0.673696     1.928441   
2090   all  Glutamatergic   998  Arhgap15           0  0.673661     2.172122   
2091   all  Glutamatergic   999     Mark2           0  0.673626     1.674353   
2092   all  Glutamatergic  1000     Dusp3           0  0.673556     1.658276   

      fold_change_detection   expression  precision  ...  population_size  \
0                  9.289078   820.463486   0.659089  ...          10207.0   
1                 13.987046   659.151566   0.730005  ...          10207.0   
2                  5.736415  2257.167753   0.514809  ...          10207.0   
3                 10.796420   588.571993   0.687830  ...          10207.0   
4                  3.607831   340.701798   0.442861  ...          10207.0   
...                     ...          ...        ...  ...              ...   
2088               1.330209   643.230145   0.794692  ...          49843.0   
2089               1.964884    86.019253   0.848298  ...          49843.0   
2090               2.024808   123.864884   0.852030  ...          49843.0   
2091               1.626757   107.760108   0.821639  ...          49843.0   
2092               1.517321   110.740179   0.812380  ...          49843.0   

      n_datasets   scSS   snSS  scCv2  snCv2  snCv3M  scCv3  snCv3Z  \
0              7   True   True   True   True    True   True    True   
1              7   True   True   True   True    True   True    True   
2              7   True   True   True   True    True   True    True   
3              7   True   True   True   True    True   True    True   
4              7   True   True   True   True    True   True    True   
...          ...    ...    ...    ...    ...     ...    ...     ...   
2088           7  False  False  False  False   False  False   False   
2089           7  False  False  False  False   False  False   False   
2090           7  False  False  False  False   False  False   False   
2091           7  False  False  False  False   False  False   False   
2092           7  False  False  False  False   False  False   False   

                 gene_id  
0     ENSMUSG00000070880  
1     ENSMUSG00000026787  
2     ENSMUSG00000062209  
3     ENSMUSG00000053519  
4     ENSMUSG00000039607  
...                  ...  
2088  ENSMUSG00000029108  
2089  ENSMUSG00000052632  
2090  ENSMUSG00000049744  
2091  ENSMUSG00000024969  
2092  ENSMUSG00000003518  

[1798 rows x 21 columns]

In [47]:
marker_list[marker_list['cell_type']!='Non-Neuronal'].drop_duplicates(subset=['gene_id'], keep=False)

group      cell_type  rank      gene  recurrence     auroc  fold_change  \
0      all      GABAergic     1      Gad1           7  0.941159   116.960472   
1      all      GABAergic     2      Gad2           7  0.928440   139.811415   
2      all      GABAergic     3     Erbb4           7  0.921449    81.717383   
3      all      GABAergic     4    Kcnip1           7  0.916919    32.252038   
4      all      GABAergic     5     Rbms3           7  0.902093    17.038869   
...    ...            ...   ...       ...         ...       ...          ...   
2088   all  Glutamatergic   996     Pcdh7           0  0.673757     1.461875   
2089   all  Glutamatergic   997     Asap2           0  0.673696     1.928441   
2090   all  Glutamatergic   998  Arhgap15           0  0.673661     2.172122   
2091   all  Glutamatergic   999     Mark2           0  0.673626     1.674353   
2092   all  Glutamatergic  1000     Dusp3           0  0.673556     1.658276   

      fold_change_detection   expression  precision  ...  population_size  \
0                  9.289078   820.463486   0.659089  ...          10207.0   
1                 13.987046   659.151566   0.730005  ...          10207.0   
2                  5.736415  2257.167753   0.514809  ...          10207.0   
3                 10.796420   588.571993   0.687830  ...          10207.0   
4                  3.607831   340.701798   0.442861  ...          10207.0   
...                     ...          ...        ...  ...              ...   
2088               1.330209   643.230145   0.794692  ...          49843.0   
2089               1.964884    86.019253   0.848298  ...          49843.0   
2090               2.024808   123.864884   0.852030  ...          49843.0   
2091               1.626757   107.760108   0.821639  ...          49843.0   
2092               1.517321   110.740179   0.812380  ...          49843.0   

      n_datasets   scSS   snSS  scCv2  snCv2  snCv3M  scCv3  snCv3Z  \
0              7   True   True   True   True    True   True    True   
1              7   True   True   True   True    True   True    True   
2              7   True   True   True   True    True   True    True   
3              7   True   True   True   True    True   True    True   
4              7   True   True   True   True    True   True    True   
...          ...    ...    ...    ...    ...     ...    ...     ...   
2088           7  False  False  False  False   False  False   False   
2089           7  False  False  False  False   False  False   False   
2090           7  False  False  False  False   False  False   False   
2091           7  False  False  False  False   False  False   False   
2092           7  False  False  False  False   False  False   False   

                 gene_id  
0     ENSMUSG00000070880  
1     ENSMUSG00000026787  
2     ENSMUSG00000062209  
3     ENSMUSG00000053519  
4     ENSMUSG00000039607  
...                  ...  
2088  ENSMUSG00000029108  
2089  ENSMUSG00000052632  
2090  ENSMUSG00000049744  
2091  ENSMUSG00000024969  
2092  ENSMUSG00000003518  

[1798 rows x 21 columns]

In [4]:


df_max_gene_inter_by_bins = pd.DataFrame(my_data, index=gene_list, columns = bins_bed['bin_id'].tolist())

df_max_gene_inter_by_bins_normalized = df_max_gene_inter_by_bins.div(df_max_gene_inter_by_bins.mean(axis=1, skipna=True), axis=0)
df_max_gene_inter_by_bins = df_max_gene_inter_by_bins_normalized






In [28]:
        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        marker_list_types = marker_list.drop_duplicates(subset=['cell_type'])['cell_type'].tolist()   
        marker_list_groups = marker_list.drop_duplicates(subset=['cell_type'])['group'].tolist() 
        

In [30]:
df_max_gene_inter_by_bins

0        1        2        3        4        5        \
ENSMUSG00000070880      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000026787      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000062209      NaN      NaN      NaN      NaN      NaN      NaN   
ENSMUSG00000053519      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000039607      0.0      0.0      0.0      0.0      0.0      0.0   
...                     ...      ...      ...      ...      ...      ...   
ENSMUSG00000021144      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000020649      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000113170      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000018931      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000016495      0.0      0.0      0.0      0.0      0.0      0.0   

                    6        7        8        9        ...  2462745  2462746  \
ENSMUSG00000070880      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000026787      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000062209      NaN      NaN      NaN      NaN  ...      0.0      0.0   
ENSMUSG00000053519      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000039607      0.0      0.0      0.0      0.0  ...      0.0      0.0   
...                     ...      ...      ...      ...  ...      ...      ...   
ENSMUSG00000021144      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000020649      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000113170      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000018931      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000016495      0.0      0.0      0.0      0.0  ...      NaN      NaN   

                    2462747  2462748  2462749  2462750  2462751  2462752  \
ENSMUSG00000070880      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000026787      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000062209      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000053519      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000039607      0.0      0.0      0.0      0.0      0.0      0.0   
...                     ...      ...      ...      ...      ...      ...   
ENSMUSG00000021144      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000020649      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000113170      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000018931      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000016495      NaN      NaN      NaN      NaN      NaN      NaN   

                    2462753  2462754  
ENSMUSG00000070880      0.0      0.0  
ENSMUSG00000026787      0.0      0.0  
ENSMUSG00000062209      0.0      0.0  
ENSMUSG00000053519      0.0      0.0  
ENSMUSG00000039607      0.0      0.0  
...                     ...      ...  
ENSMUSG00000021144      0.0      0.0  
ENSMUSG00000020649      0.0      0.0  
ENSMUSG00000113170      0.0      0.0  
ENSMUSG00000018931      0.0      0.0  
ENSMUSG00000016495      NaN      NaN  

[11023 rows x 2462755 columns]

In [29]:
    df_class = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_cluster_markers.csv')

    class_dict = dict(zip(df_class.cell_type,df_class.group))

    
    subclass_list = [class_dict[x] for x in marker_list_types]
    df_max_gene_inter_by_bins['subclass'] = subclass_list
    
    df_class = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_subclass_markers.csv')

    class_dict = dict(zip(df_class.cell_type,df_class.group))
    class_dict['L4/5 IT'] = 'Glutamatergic'
    class_dict['L5 PT'] = 'Glutamatergic'
    class_list = [class_dict[x] for x in subclass_list]
    df_max_gene_inter_by_bins['class'] = [class_dict[x] for x in df_max_gene_inter_by_bins['subclass'].tolist()]
    

ValueError: Length of values (86) does not match length of index (11023)

In [34]:
import os

            
import os
from scipy.stats import mannwhitneyu


number_of_genes_list = [200]
marker_level_list = ['cluster']
#number_of_genes_list = [ 1000, 'opt', 10, 200]
#marker_level_list = ['class', 'subclass', 'cluster']
for number_of_genes in number_of_genes_list:
    for marker_level in marker_level_list:
        
        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/mouse_geneid_symbol.txt',sep='\t', names=['gene_id', 'gene'])
        #df_ensg_name['gene'] = df_ensg_name['gene'].str.upper()
        marker_list = marker_list.merge(df_ensg_name.drop_duplicates(subset=['gene']), right_on='gene', left_on='gene') 

        #marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/{species}/{marker_level}_markers_top1000.csv.gz', skiprows=1)
        #df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
        #marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
        marker_list = marker_list[marker_list['gene_id'].isin(tot_g)]
        #marker_list = marker_list[marker_list['rank'] < number_of_genes]
        all_cell_types = marker_list.drop_duplicates(['cell_type'])['cell_type'].tolist()
        

        df2_list = []
                    

                
        for group2 in all_cell_types:
                df2_list.append(marker_list[marker_list['cell_type']==group2].sort_values(by=['rank']).head(number_of_genes))

        marker_list=pd.concat(df2_list)

        marker_table = marker_list.pivot_table(index='gene_id', columns='cell_type', values='rank', aggfunc='sum')

        marker_table.fillna(0, inplace=True)
                    
        marker_table[marker_table != 0] = 1

        all_markers = marker_table.index.tolist()
                    


        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        marker_list_types = marker_list.drop_duplicates(subset=['cell_type'])['cell_type'].tolist()   
        marker_list_groups = marker_list.drop_duplicates(subset=['cell_type'])['group'].tolist()   
        
        
        
        df_class = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_cluster_markers.csv')

        class_dict = dict(zip(df_class.cell_type,df_class.group))


        subclass_list = [class_dict[x] for x in marker_list_types]

        df_class = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_subclass_markers.csv')

        class_dict = dict(zip(df_class.cell_type,df_class.group))
        class_dict['L4/5 IT'] = 'Glutamatergic'
        class_dict['L5 PT'] = 'Glutamatergic'
        class_list = [class_dict[x] for x in subclass_list]
        

    
        df_list_mean = []

        cell_type_list_order = []
        
        df_list_p_val = []
        
        #all_cell_types  = ['Glutamatergic', 'GABAergic']
        for cell_type in ['Glutamatergic', 'GABAergic']:
            for cell_type_2 in ['Glutamatergic', 'GABAergic']:
                
                if cell_type != cell_type:
                
                    marker_genes_group_1 = []
                    marker_genes_group_2 = []


                    for group_name, cell_type_3 in zip(class_list, marker_list_types):


                        if group_name==cell_type:
                            print (cell_type_3)
                            marker_genes_group_1.append(marker_table[marker_table[cell_type_3] == 1].index.tolist())
                        else:
                            print (cell_type_3)
                            marker_genes_group_2.append(marker_table[marker_table[cell_type_3] == 1].index.tolist())



                    print (len(marker_genes_group_1))
                    print (len(marker_genes_group_2))

                    df_mean = []

                    for groupname_list in marker_genes_group_1:
                        df_mean.append(df_max_gene_inter_by_bins.loc[groupname_list, :].mean().reset_index().set_index('index').T)

                    df_max_gene_whole_group_1 = pd.concat(df_mean)

                    print (df_max_gene_whole_group_1)

                    df_mean = []

                    for groupname_list in marker_genes_group_2:
                        df_mean.append(df_max_gene_inter_by_bins.loc[groupname_list, :].mean().reset_index().set_index('index').T)

                    df_max_gene_whole_group_2 = pd.concat(df_mean)
                    
                
                
            

                #df_max_gene_whole_group_1 = df_max_gene_inter_by_bins.loc[marker_genes_group_1, :]



                #df_max_gene_whole_group_2 = df_max_gene_inter_by_bins.loc[marker_genes_group_2, :]






/grid/gillis/home/lohia/.conda/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (15,16) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,
/grid/gillis/home/lohia/.conda/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (15,16) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


L2/3 IT_1
L2/3 IT_2
L2/3 IT_3
L4/5 IT_1
L4/5 IT_2
L5 IT_1
L5 IT_2
L5 IT_3
L5 IT_4
L5 PT_1
L5 PT_2
L5 PT_3
L5 PT_4
L5/6 NP CT
L5/6 NP_1
L5/6 NP_2
L5/6 NP_3
L6 CT Cpa6
L6 CT Gpr139
L6 CT Grp
L6 CT Kit_1
L6 CT Kit_2
L6 CT Pou3f2
L6 IT_1
L6 IT_2
L6b Col6a1
L6b Kcnip1
L6b Ror1
L6b Shisa6_1
L6b Shisa6_2
Lamp5 Egln3_1
Lamp5 Egln3_2
Lamp5 Egln3_3
Lamp5 Lhx6
Lamp5 Pax6
Lamp5 Pdlim5_1
Lamp5 Pdlim5_2
Lamp5 Slc35d3
Pvalb Calb1_1
Pvalb Calb1_2
Pvalb Egfem1
Pvalb Gabrg1
Pvalb Gpr149
Pvalb Il1rapl2
Pvalb Kank4
Pvalb Reln
Pvalb Vipr2_1
Pvalb Vipr2_2
Sncg Calb1_1
Sncg Calb1_2
Sncg Col14a1
Sncg Npy2r
Sncg Slc17a8
Vip Sncg
Sst C1ql3_1
Sst C1ql3_2
Sst Calb2
Sst Crhr2_1
Sst Crhr2_2
Sst Etv1
Sst Hpse
Sst Htr1a
Sst Myh8_1
Sst Myh8_2
Sst Myh8_3
Sst Pappa
Sst Penk
Sst Pvalb Calb2
Sst Pvalb Etv1
Sst Tac2
Sst Th_1
Sst Th_2
Sst Th_3
Vip C1ql1
Vip Chat_1
Vip Chat_2
Vip Gpc3
Vip Htr1f
Vip Igfbp6_1
Vip Igfbp6_2
Vip Mybpc1_1
Vip Mybpc1_2
Vip Mybpc1_3
Vip Serpinf1_1
Vip Serpinf1_2
Vip Serpinf1_3
30
56


NameError: name 'group_max' is not defined

In [33]:
df_max_gene_whole_group_1

0        1        2        3        4        5        \
ENSMUSG00000000632      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000000794      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000000861      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000002107      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000002489      0.0      0.0      0.0      0.0      0.0      0.0   
...                     ...      ...      ...      ...      ...      ...   
ENSMUSG00000090667      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000092094      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000097452      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000097767      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000097929      0.0      0.0      0.0      0.0      0.0      0.0   

                    6        7        8        9        ...  2462745  2462746  \
ENSMUSG00000000632      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000000794      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000000861      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000002107      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000002489      0.0      0.0      0.0      0.0  ...      0.0      0.0   
...                     ...      ...      ...      ...  ...      ...      ...   
ENSMUSG00000090667      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000092094      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000097452      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000097767      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000097929      0.0      0.0      0.0      0.0  ...      0.0      0.0   

                    2462747  2462748  2462749  2462750  2462751  2462752  \
ENSMUSG00000000632      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000000794      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000000861      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000002107      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000002489      0.0      0.0      0.0      0.0      0.0      0.0   
...                     ...      ...      ...      ...      ...      ...   
ENSMUSG00000090667      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000092094      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000097452      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000097767      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000097929      0.0      0.0      0.0      0.0      0.0      0.0   

                    2462753  2462754  
ENSMUSG00000000632      0.0      0.0  
ENSMUSG00000000794      0.0      0.0  
ENSMUSG00000000861      0.0      0.0  
ENSMUSG00000002107      0.0      0.0  
ENSMUSG00000002489      0.0      0.0  
...                     ...      ...  
ENSMUSG00000090667      0.0      0.0  
ENSMUSG00000092094      0.0      0.0  
ENSMUSG00000097452      0.0      0.0  
ENSMUSG00000097767      0.0      0.0  
ENSMUSG00000097929      0.0      0.0  

[6000 rows x 2462755 columns]

In [35]:
df_max_gene_whole_group_1 = pd.concat(df_mean)

In [36]:
df_max_gene_whole_group_1

index  0        1        2        3        4        5        6        7        \
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0      0.0      0.0      0.0      0.0      0.0      0.0   

index  8        9        ...  2462745  2462746  2462747  2462748  2462749  \
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  ...      0.0      0.0      0.0      0.0      0.0   
0          0.0      0.0  

In [25]:

    for groupname in ['Glutamatergic', 'GABAergic']:
        
        #d2 = df_concat_list_mean_nn_by_bins_normalized[df_concat_list_mean_nn_by_bins_normalized.index.isin(ll)]
        d2 = df_concat_list_mean_nn_by_bins_normalized
        df_concat_vip = d2[d2["class"] == groupname].loc[:, :2462754].mean().reset_index().set_index('index').T
        df_concat_vip['group'] = groupname
        group_max.append(df_concat_vip)

    df_group_max = pd.concat(group_max)

cell_type           L2/3 IT_1  L2/3 IT_2  L2/3 IT_3  L4/5 IT_1  L4/5 IT_2  \
gene_id                                                                     
ENSMUSG00000000058        0.0        0.0        0.0        0.0        0.0   
ENSMUSG00000000120        0.0        0.0        0.0        0.0        0.0   
ENSMUSG00000000125        0.0        0.0        0.0        0.0        0.0   
ENSMUSG00000000126        0.0        0.0        0.0        0.0        0.0   
ENSMUSG00000000168        0.0        0.0        0.0        0.0        0.0   
...                       ...        ...        ...        ...        ...   
ENSMUSG00000112278        0.0        0.0        0.0        0.0        0.0   
ENSMUSG00000112925        0.0        0.0        0.0        0.0        0.0   
ENSMUSG00000113313        0.0        0.0        1.0        0.0        0.0   
ENSMUSG00000114469        0.0        1.0        0.0        0.0        0.0   
ENSMUSG00000115529        0.0        0.0        0.0        0.0        0.0   

cell_type           L5 IT_1  L5 IT_2  L5 IT_3  L5 IT_4  L5 PT_1  ...  \
gene_id                                                          ...   
ENSMUSG00000000058      0.0      0.0      0.0      0.0      0.0  ...   
ENSMUSG00000000120      0.0      0.0      0.0      0.0      0.0  ...   
ENSMUSG00000000125      0.0      0.0      0.0      0.0      0.0  ...   
ENSMUSG00000000126      0.0      0.0      0.0      0.0      0.0  ...   
ENSMUSG00000000168      0.0      0.0      0.0      0.0      0.0  ...   
...                     ...      ...      ...      ...      ...  ...   
ENSMUSG00000112278      0.0      0.0      0.0      0.0      0.0  ...   
ENSMUSG00000112925      0.0      0.0      0.0      0.0      0.0  ...   
ENSMUSG00000113313      0.0      0.0      0.0      0.0      0.0  ...   
ENSMUSG00000114469      0.0      0.0      0.0      0.0      0.0  ...   
ENSMUSG00000115529      0.0      0.0      0.0      0.0      0.0  ...   

cell_type           Vip Htr1f  Vip Igfbp6_1  Vip Igfbp6_2  Vip Mybpc1_1  \
gene_id                                                                   
ENSMUSG00000000058        0.0           0.0           0.0           0.0   
ENSMUSG00000000120        0.0           0.0           0.0           0.0   
ENSMUSG00000000125        0.0           0.0           0.0           0.0   
ENSMUSG00000000126        0.0           0.0           0.0           0.0   
ENSMUSG00000000168        0.0           0.0           0.0           0.0   
...                       ...           ...           ...           ...   
ENSMUSG00000112278        0.0           0.0           0.0           0.0   
ENSMUSG00000112925        0.0           0.0           0.0           0.0   
ENSMUSG00000113313        0.0           0.0           0.0           0.0   
ENSMUSG00000114469        0.0           0.0           0.0           0.0   
ENSMUSG00000115529        0.0           0.0           0.0           0.0   

cell_type           Vip Mybpc1_2  Vip Mybpc1_3  Vip Serpinf1_1  \
gene_id                                                          
ENSMUSG00000000058           0.0           0.0             0.0   
ENSMUSG00000000120           0.0           0.0             0.0   
ENSMUSG00000000125           0.0           0.0             0.0   
ENSMUSG00000000126           0.0           0.0             0.0   
ENSMUSG00000000168           0.0           0.0             0.0   
...                          ...           ...             ...   
ENSMUSG00000112278           0.0           0.0             0.0   
ENSMUSG00000112925           0.0           0.0             0.0   
ENSMUSG00000113313           0.0           0.0             0.0   
ENSMUSG00000114469           0.0           0.0             0.0   
ENSMUSG00000115529           0.0           0.0             0.0   

cell_type           Vip Serpinf1_2  Vip Serpinf1_3  Vip Sncg  
gene_id                                                       
ENSMUSG00000000058             0.0             0.0       0.0  
ENSMUSG00000000120             0.0   

In [26]:
df_max_gene_inter_by_bins.mean()

0        1        2        3        4        5        \
ENSMUSG00000070880      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000026787      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000062209      NaN      NaN      NaN      NaN      NaN      NaN   
ENSMUSG00000053519      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000039607      0.0      0.0      0.0      0.0      0.0      0.0   
...                     ...      ...      ...      ...      ...      ...   
ENSMUSG00000021144      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000020649      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000113170      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000018931      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000016495      0.0      0.0      0.0      0.0      0.0      0.0   

                    6        7        8        9        ...  2462745  2462746  \
ENSMUSG00000070880      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000026787      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000062209      NaN      NaN      NaN      NaN  ...      0.0      0.0   
ENSMUSG00000053519      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000039607      0.0      0.0      0.0      0.0  ...      0.0      0.0   
...                     ...      ...      ...      ...  ...      ...      ...   
ENSMUSG00000021144      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000020649      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000113170      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000018931      0.0      0.0      0.0      0.0  ...      0.0      0.0   
ENSMUSG00000016495      0.0      0.0      0.0      0.0  ...      NaN      NaN   

                    2462747  2462748  2462749  2462750  2462751  2462752  \
ENSMUSG00000070880      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000026787      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000062209      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000053519      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000039607      0.0      0.0      0.0      0.0      0.0      0.0   
...                     ...      ...      ...      ...      ...      ...   
ENSMUSG00000021144      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000020649      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000113170      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000018931      0.0      0.0      0.0      0.0      0.0      0.0   
ENSMUSG00000016495      NaN      NaN      NaN      NaN      NaN      NaN   

                    2462753  2462754  
ENSMUSG00000070880      0.0      0.0  
ENSMUSG00000026787      0.0      0.0  
ENSMUSG00000062209      0.0      0.0  
ENSMUSG00000053519      0.0      0.0  
ENSMUSG00000039607      0.0      0.0  
...                     ...      ...  
ENSMUSG00000021144      0.0      0.0  
ENSMUSG00000020649      0.0      0.0  
ENSMUSG00000113170      0.0      0.0  
ENSMUSG00000018931      0.0      0.0  
ENSMUSG00000016495      NaN      NaN  

[11023 rows x 2462755 columns]

In [48]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py


SRP_name = 'aggregates'
resolution = '1kbp_raw' 
species= 'mouse'


def calc_auroc (df_trial,predicted_score='predicted_score'):
    df_trial = df_trial.sort_values(by=[predicted_score], ascending=False)
    rank_abs = lambda x: stats.rankdata(x)
    predicts2 = np.apply_along_axis(rank_abs, 0, df_trial[predicted_score].values)
    df_trial['p'] = [y if x==1 else 0 for x,y in zip(df_trial['true_pos'], predicts2)]
    #print (df_trial['p'].sum())
    if df_trial['true_neg'].sum() == 0 or df_trial['true_pos'].sum() == 0:
        return np.nan
    else:
        return (((df_trial['p'].sum() /df_trial['true_pos'].sum() )- (df_trial['true_pos'].sum() + 1)/2)) / df_trial['true_neg'].sum()


exp_file_path=f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/spr/hic_gene_corr_inter_excluding_intra_chrom_pairs_hicexp.h5'
jac_sim_spr = hm.hiCMatrix(exp_file_path)
all_genes_spr = [x[3].decode() for x in jac_sim_spr.cut_intervals]
df_jac_corr = pd.DataFrame(jac_sim_spr.matrix.toarray() ,  index=all_genes_spr, columns = all_genes_spr)
  

input_path=f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/'
bins_bed = pd.read_csv(f'{input_path}/all_bins.bed', names=['chr', 'start', 'end', 'bin_id'])
bins_bed['bin_id'] = bins_bed.index
  
chr_list = bins_bed.drop_duplicates(subset=['chr'])['chr'].tolist()
chrom_index_list = {}
for chrom in chr_list:
      st = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[0]
      en = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[-1]
      chrom_index_list[chrom] = list(range(st, en+1))
gene_bed = pd.read_csv(f'{input_path}/all_gene.bed', names=['chr', 'start_bin', 'end_bin', 'gene'])


chrom_index_list_intra = {}
for chrom in chr_list:
    index_list = []
    for chrom2 in chr_list:
        if chrom2 != chrom:
            index_list.extend(chrom_index_list[chrom2])
        
    
    chrom_index_list_intra[chrom] = index_list

marker_list = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_cluster_markers.csv')

all_markers_df = []
for marker_type in ['class', 'subclass', 'cluster']:
	marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_type}_markers.csv')
	all_markers_df.append(marker_list)

marker_list = pd.concat(all_markers_df)
marker_list = marker_list.drop_duplicates(subset=['gene'])
df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/mouse_geneid_symbol.txt',sep='\t', names=['gene_id', 'gene'])
#df_ensg_name['gene'] = df_ensg_name['gene'].str.upper()
marker_list = marker_list.merge(df_ensg_name.drop_duplicates(subset=['gene']), right_on='gene', left_on='gene') 
#df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
#marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
#marker_list = marker_list.drop_duplicates(subset=['Ensembl_gene_identifier'])
marker_list = marker_list.drop_duplicates(subset=['gene_id'])



with h5py.File(f'{input_path}/hic_gene_gw_none_by_allbins_none.h5', 'r') as hf:
        tot_g = (list(hf.keys()))

all_background_markers = list(set(all_genes_spr) -  set(marker_list['gene_id'].tolist())) + marker_list['gene_id'].tolist()
all_background_markers = marker_list['gene_id'].tolist()
#all_background_markers = marker_list['cell_type'] != Non-Neuronal['gene_id'].tolist()

marker_contacts_list_inter = []

gene_list = []
with h5py.File(f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/hic_gene_gw_none_by_allbins_none.h5', 'r') as hf:
                   
                   for key in all_background_markers:
                    if key in tot_g:
                            gene_list.append(key)
                            gene_chrom = gene_bed[gene_bed['gene'] == key]['chr'].values[0]
                            #which ever chrom the gene falls into, those bins should be nan
                            my_data = hf[key][()]
                            my_data = my_data.astype('float64')
                            my_data[chrom_index_list_intra[gene_chrom]] = np.nan
                            marker_contacts_list_inter.append(my_data)
                            
                            
my_data = np.array(marker_contacts_list_inter)


df_max_gene_inter_by_bins = pd.DataFrame(my_data, index=gene_list, columns = bins_bed['bin_id'].tolist())

df_max_gene_inter_by_bins_normalized = df_max_gene_inter_by_bins.div(df_max_gene_inter_by_bins.mean(axis=1, skipna=True), axis=0)
df_max_gene_inter_by_bins = df_max_gene_inter_by_bins_normalized

df_max_gene_inter_by_bins_sum = df_max_gene_inter_by_bins.sum().reset_index()

df_max_gene_inter_by_bins_sum_mean = df_max_gene_inter_by_bins.mean().reset_index()

#outfile_name = f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/background_sum_gene_nor_all_back.csv'
#df_max_gene_inter_by_bins_sum.to_csv(outfile_name, index=False)
#outfile_name = f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/background_mean_gene_nor_all_back.csv'
#df_max_gene_inter_by_bins_sum_mean.to_csv(outfile_name, index=False)


import os
number_of_genes_list = [ 1000, 'opt', 10, 200]
number_of_genes_list = [ 1000 ]
marker_level_list = ['class', 'subclass', 'cluster']
marker_level_list = ['class']

for number_of_genes in number_of_genes_list:
    for marker_level in marker_level_list:
        
        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/mouse_geneid_symbol.txt',sep='\t', names=['gene_id', 'gene'])
        #df_ensg_name['gene'] = df_ensg_name['gene'].str.upper()
        marker_list = marker_list.merge(df_ensg_name.drop_duplicates(subset=['gene']), right_on='gene', left_on='gene') 

        #marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/{species}/{marker_level}_markers_top1000.csv.gz', skiprows=1)
        #df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
        #marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
        #marker_list = marker_list[marker_list['gene_id'].isin(all_genes_spr)]
        marker_list = marker_list[marker_list['gene_id'].isin(tot_g)]
        
        #marker_list = marker_list[marker_list['rank'] < number_of_genes]
        all_cell_types = marker_list.drop_duplicates(['cell_type'])['cell_type'].tolist()
        df2_list = []
                    

                
        for group2 in all_cell_types:
            
            if number_of_genes == 'opt':
            
                number_of_marker = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/optimal_number_markers.csv').sort_values(by=['f1']).drop_duplicates(subset=['marker_set'], keep='last')

                try:
                    number_of_genes_optimal = number_of_marker[number_of_marker['marker_set'] == group2]['n_genes'].values[0]
                except:
                    number_of_genes_optimal = 0
                df2_list.append(marker_list[((marker_list['cell_type']==group2) & (marker_list['rank']<=number_of_genes_optimal))])
            else:
                df2_list.append(marker_list[marker_list['cell_type']==group2].sort_values(by=['rank']).head(number_of_genes))

        marker_list=pd.concat(df2_list)

        marker_table = marker_list.pivot_table(index='gene_id', columns='cell_type', values='rank', aggfunc='sum')

        marker_table.fillna(0, inplace=True)
                    
        marker_table[marker_table != 0] = 1

        all_markers = marker_table.index.tolist()
                    


        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        marker_list_types = marker_list.drop_duplicates(subset=['cell_type'])['cell_type'].tolist()   
        marker_list_groups = marker_list.drop_duplicates(subset=['cell_type'])['group'].tolist()   
        df_list_mean = []

        cell_type_list_order = []
        


        for group, cell_type in zip(marker_list_groups, marker_list_types):
            
            try:
            
            
                marker_genes_group = marker_table[marker_table[cell_type] == 1].index.tolist()

                df_tmp = df_max_gene_inter_by_bins.loc[marker_genes_group, :].mean(skipna=True).reset_index()

                df_tmp= df_tmp.set_index('index')
                df_tmp.rename(columns = {0:'mean_cell_type'}, inplace = True)

                d2 = df_tmp[['mean_cell_type']].T
                cell_type_list_order.append(cell_type)
                #d2['cell_type'] = cell_type
                #d2['subclass'] = group
                #d2['class'] = class_dict[group]

                df_list_mean.append(d2)
            except:
                pass
            #print (cell_type)
            
        df_concat_list_mean_nn = pd.concat(df_list_mean)
        column_list = df_concat_list_mean_nn.columns.tolist()
        print (number_of_genes)

        from umap import UMAP
        import plotly.express as px

        df = df_concat_list_mean_nn.dropna(axis=1)


        features = df

        umap_2d = UMAP(n_components=2, init='random', random_state=0)


        proj_2d = umap_2d.fit_transform(features)


        j = df_concat_list_mean_nn.to_numpy()
        
        

        outfile_name = f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/{marker_level}_{number_of_genes}_contacts_gene_nor_all_back_intra.h5'
        
        if os.path.isfile(outfile_name):
            os.remove(outfile_name)
        
        with h5py.File(outfile_name, 'a') as hf:
                            


            hf.create_dataset('type_contacts',data=j)
            hf.create_dataset('type_list',data=cell_type_list_order)
            hf.create_dataset('column_list',data=column_list)
            

            

        outfile_name = f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/{marker_level}_{number_of_genes}_proj_2d_gene_nor_all_back_intra.h5'
        
        if os.path.isfile(outfile_name):
            os.remove(outfile_name)
        with h5py.File(outfile_name, 'a') as hf:
                            

            hf.create_dataset('proj_2d',data=proj_2d)
            hf.create_dataset('type_list',data=cell_type_list_order)
            
import os
from scipy.stats import mannwhitneyu



                        
                        
number_of_genes_list = [1000, 800, 500]
marker_level_list = ['class']
#number_of_genes_list = [ 1000, 'opt', 10, 200]
#marker_level_list = ['class', 'subclass', 'cluster']
for number_of_genes in number_of_genes_list:
    for marker_level in marker_level_list:
        
        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/mouse_geneid_symbol.txt',sep='\t', names=['gene_id', 'gene'])
        #df_ensg_name['gene'] = df_ensg_name['gene'].str.upper()
        marker_list = marker_list.merge(df_ensg_name.drop_duplicates(subset=['gene']), right_on='gene', left_on='gene') 

        #marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/{species}/{marker_level}_markers_top1000.csv.gz', skiprows=1)
        #df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
        #marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
        #marker_list = marker_list[marker_list['gene_id'].isin(all_genes_spr)]
        marker_list = marker_list[marker_list['gene_id'].isin(tot_g)]
        #marker_list = marker_list[marker_list['rank'] < number_of_genes]
        all_cell_types = marker_list.drop_duplicates(['cell_type'])['cell_type'].tolist()
        df2_list = []
                    

                
        for group2 in all_cell_types:
                df2_list.append(marker_list[marker_list['cell_type']==group2].sort_values(by=['rank']).head(number_of_genes))

        marker_list=pd.concat(df2_list)

        marker_table = marker_list.pivot_table(index='gene_id', columns='cell_type', values='rank', aggfunc='sum')

        marker_table.fillna(0, inplace=True)
                    
        marker_table[marker_table != 0] = 1

        all_markers = marker_table.index.tolist()
                    


        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        marker_list_types = marker_list.drop_duplicates(subset=['cell_type'])['cell_type'].tolist()   
        marker_list_groups = marker_list.drop_duplicates(subset=['cell_type'])['group'].tolist()   
        df_list_mean = []

        cell_type_list_order = []
        
        df_list_p_val = []
        
        #all_cell_types  = ['Glutamatergic', 'GABAergic']

        for group, cell_type in zip(marker_list_groups, marker_list_types):
            for cell_type_2 in marker_list_types:
                
                if cell_type != cell_type_2:
            
            
            
                    marker_genes_group = marker_table[marker_table[cell_type] == 1].index.tolist()

                    df_max_gene_whole_group_1 = df_max_gene_inter_by_bins.loc[marker_genes_group, :]

                    marker_genes_group = marker_table[marker_table[cell_type] != 1].index.tolist()

                    df_max_gene_whole_group_2 = df_max_gene_inter_by_bins.loc[marker_genes_group, :]

                    def addData(x):
                        try:
                            U, p_val = mannwhitneyu(x.dropna().tolist(), df_max_gene_whole_group_2[x.name].dropna().tolist(), alternative="greater")
                            return p_val
                        except:
                            return np.nan


                    new_df = df_max_gene_whole_group_1.apply(addData)
                    df_list_p_val.append(new_df)
                    cell_type_list_order.append(cell_type)
                    column_list = df_max_gene_whole_group_1.columns.tolist()
                    j = new_df.to_numpy()
                    cell_type_name = cell_type.replace('/', "_")
                    outfile_name = f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/{marker_level}_{number_of_genes}_p_val_gene_nor_all_back_{cell_type}_vs_remaining_class_intra.h5'

                    if os.path.isfile(outfile_name):
                        os.remove(outfile_name)

                    with h5py.File(outfile_name, 'a') as hf:



                        hf.create_dataset('type_contacts',data=j)
                        hf.create_dataset('type_list',data=cell_type)
                        hf.create_dataset('type_list_2',data=cell_type_2)
                        hf.create_dataset('column_list',data=column_list)


                        
                        
number_of_genes_list = [100, 800, 500]
marker_level_list = ['class']
#number_of_genes_list = [ 1000, 'opt', 10, 200]
#marker_level_list = ['class', 'subclass', 'cluster']
for number_of_genes in number_of_genes_list:
    for marker_level in marker_level_list:
        
        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/mouse_geneid_symbol.txt',sep='\t', names=['gene_id', 'gene'])
        #df_ensg_name['gene'] = df_ensg_name['gene'].str.upper()
        marker_list = marker_list.merge(df_ensg_name.drop_duplicates(subset=['gene']), right_on='gene', left_on='gene') 

        #marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/{species}/{marker_level}_markers_top1000.csv.gz', skiprows=1)
        #df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
        #marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
        #marker_list = marker_list[marker_list['gene_id'].isin(all_genes_spr)]
        marker_list = marker_list[marker_list['gene_id'].isin(tot_g)]
        #marker_list = marker_list[marker_list['rank'] < number_of_genes]
        all_cell_types = marker_list.drop_duplicates(['cell_type'])['cell_type'].tolist()
        df2_list = []
                    

                
        for group2 in all_cell_types:
                df2_list.append(marker_list[marker_list['cell_type']==group2].sort_values(by=['rank']).head(number_of_genes))

        marker_list=pd.concat(df2_list)

        marker_table = marker_list.pivot_table(index='gene_id', columns='cell_type', values='rank', aggfunc='sum')

        marker_table.fillna(0, inplace=True)
                    
        marker_table[marker_table != 0] = 1

        all_markers = marker_table.index.tolist()
                    


        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        marker_list_types = marker_list.drop_duplicates(subset=['cell_type'])['cell_type'].tolist()   
        marker_list_groups = marker_list.drop_duplicates(subset=['cell_type'])['group'].tolist()   
        df_list_mean = []

        cell_type_list_order = []
        
        df_list_p_val = []
        
        #all_cell_types  = ['Glutamatergic', 'GABAergic']

        for group, cell_type in zip(marker_list_groups, marker_list_types):
            for cell_type_2 in marker_list_types:
                
                if cell_type != cell_type_2:
            
            
            
                    marker_genes_group = marker_table[marker_table[cell_type] == 1].index.tolist()

                    df_max_gene_whole_group_1 = df_max_gene_inter_by_bins.loc[marker_genes_group, :]

                    marker_genes_group = marker_table[marker_table[cell_type_2] == 1].index.tolist()

                    df_max_gene_whole_group_2 = df_max_gene_inter_by_bins.loc[marker_genes_group, :]

                    def addData(x):
                        try:
                            U, p_val = mannwhitneyu(x.dropna().tolist(), df_max_gene_whole_group_2[x.name].dropna().tolist(), alternative="greater")
                            return p_val
                        except:
                            return np.nan


                    new_df = df_max_gene_whole_group_1.apply(addData)
                    df_list_p_val.append(new_df)
                    cell_type_list_order.append(cell_type)
                    column_list = df_max_gene_whole_group_1.columns.tolist()
                    j = new_df.to_numpy()
                    cell_type_name = cell_type.replace('/', "_")
                    outfile_name = f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/{marker_level}_{number_of_genes}_p_val_gene_nor_all_back_{cell_type}_vs_{cell_type_2}_class_intra.h5'

                    if os.path.isfile(outfile_name):
                        os.remove(outfile_name)

                    with h5py.File(outfile_name, 'a') as hf:



                        hf.create_dataset('type_contacts',data=j)
                        hf.create_dataset('type_list',data=cell_type)
                        hf.create_dataset('type_list_2',data=cell_type_2)
                        hf.create_dataset('column_list',data=column_list)
                        
                        

/grid/gillis/home/lohia/.conda/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (15,16) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


1000


/grid/gillis/home/lohia/.conda/envs/hicexplorer/lib/python3.8/site-packages/umap/umap_.py:2344: UserWarning: n_neighbors is larger than the dataset size; truncating to X.shape[0] - 1
  warn(


KeyboardInterrupt: 

In [49]:
from hicmatrix import HiCMatrix as hm
from hicmatrix.lib import MatrixFileHandler
import numpy as np
import pandas as pd
from scipy import stats, sparse
import bottleneck
from scipy.stats import mannwhitneyu
import h5py


SRP_name = 'aggregates'
resolution = '1kbp_raw' 
species= 'mouse'


def calc_auroc (df_trial,predicted_score='predicted_score'):
    df_trial = df_trial.sort_values(by=[predicted_score], ascending=False)
    rank_abs = lambda x: stats.rankdata(x)
    predicts2 = np.apply_along_axis(rank_abs, 0, df_trial[predicted_score].values)
    df_trial['p'] = [y if x==1 else 0 for x,y in zip(df_trial['true_pos'], predicts2)]
    #print (df_trial['p'].sum())
    if df_trial['true_neg'].sum() == 0 or df_trial['true_pos'].sum() == 0:
        return np.nan
    else:
        return (((df_trial['p'].sum() /df_trial['true_pos'].sum() )- (df_trial['true_pos'].sum() + 1)/2)) / df_trial['true_neg'].sum()


exp_file_path=f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/spr/hic_gene_corr_inter_excluding_intra_chrom_pairs_hicexp.h5'
jac_sim_spr = hm.hiCMatrix(exp_file_path)
all_genes_spr = [x[3].decode() for x in jac_sim_spr.cut_intervals]
df_jac_corr = pd.DataFrame(jac_sim_spr.matrix.toarray() ,  index=all_genes_spr, columns = all_genes_spr)
  

input_path=f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/'
bins_bed = pd.read_csv(f'{input_path}/all_bins.bed', names=['chr', 'start', 'end', 'bin_id'])
bins_bed['bin_id'] = bins_bed.index
  
chr_list = bins_bed.drop_duplicates(subset=['chr'])['chr'].tolist()
chrom_index_list = {}
for chrom in chr_list:
      st = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[0]
      en = bins_bed[bins_bed['chr'] == chrom]['bin_id'].tolist()[-1]
      chrom_index_list[chrom] = list(range(st, en+1))
gene_bed = pd.read_csv(f'{input_path}/all_gene.bed', names=['chr', 'start_bin', 'end_bin', 'gene'])



marker_list = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_cluster_markers.csv')

all_markers_df = []
for marker_type in ['class', 'subclass', 'cluster']:
	marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_type}_markers.csv')
	all_markers_df.append(marker_list)

marker_list = pd.concat(all_markers_df)
marker_list = marker_list.drop_duplicates(subset=['gene'])
df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/mouse_geneid_symbol.txt',sep='\t', names=['gene_id', 'gene'])
#df_ensg_name['gene'] = df_ensg_name['gene'].str.upper()
marker_list = marker_list.merge(df_ensg_name.drop_duplicates(subset=['gene']), right_on='gene', left_on='gene') 
#df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
#marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
#marker_list = marker_list.drop_duplicates(subset=['Ensembl_gene_identifier'])
marker_list = marker_list.drop_duplicates(subset=['gene_id'])



with h5py.File(f'{input_path}/hic_gene_gw_none_by_allbins_none.h5', 'r') as hf:
        tot_g = (list(hf.keys()))

all_background_markers = list(set(all_genes_spr) -  set(marker_list['gene_id'].tolist())) + marker_list['gene_id'].tolist()
all_background_markers = marker_list['gene_id'].tolist()
#all_background_markers = marker_list['cell_type'] != Non-Neuronal['gene_id'].tolist()

marker_contacts_list_inter = []

gene_list = []
with h5py.File(f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/hic_gene_gw_none_by_allbins_none.h5', 'r') as hf:
                   
                   for key in all_background_markers:
                    if key in tot_g:
                            gene_list.append(key)
                            gene_chrom = gene_bed[gene_bed['gene'] == key]['chr'].values[0]
                            #which ever chrom the gene falls into, those bins should be nan
                            my_data = hf[key][()]
                            my_data = my_data.astype('float64')
                            my_data[chrom_index_list[gene_chrom]] = np.nan
                            marker_contacts_list_inter.append(my_data)
                            
                            
my_data = np.array(marker_contacts_list_inter)

df_max_gene_inter_by_bins = pd.DataFrame(my_data, index=gene_list, columns = bins_bed['bin_id'].tolist())

df_max_gene_inter_by_bins_normalized = df_max_gene_inter_by_bins.div(df_max_gene_inter_by_bins.mean(axis=1, skipna=True), axis=0)
df_max_gene_inter_by_bins = df_max_gene_inter_by_bins_normalized

df_max_gene_inter_by_bins_sum = df_max_gene_inter_by_bins.sum().reset_index()

df_max_gene_inter_by_bins_sum_mean = df_max_gene_inter_by_bins.mean().reset_index()

#outfile_name = f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/background_sum_gene_nor_all_back.csv'
#df_max_gene_inter_by_bins_sum.to_csv(outfile_name, index=False)
#outfile_name = f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/background_mean_gene_nor_all_back.csv'
#df_max_gene_inter_by_bins_sum_mean.to_csv(outfile_name, index=False)





/grid/gillis/home/lohia/.conda/envs/hicexplorer/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3169: DtypeWarning: Columns (15,16) have mixed types.Specify dtype option on import or set low_memory=False.
  has_raised = await self.run_ast_nodes(code_ast.body, cell_name,


KeyboardInterrupt: 

In [52]:
k

NameError: name 'k' is not defined

In [ ]:
import os
from scipy import stats


number_of_genes_list = [1000]
marker_level_list = ['class']
#number_of_genes_list = [ 1000, 'opt', 10, 200]
#marker_level_list = ['class', 'subclass', 'cluster']
for number_of_genes in number_of_genes_list:
    for marker_level in marker_level_list:
        
        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/mouse_geneid_symbol.txt',sep='\t', names=['gene_id', 'gene'])
        #df_ensg_name['gene'] = df_ensg_name['gene'].str.upper()
        marker_list = marker_list.merge(df_ensg_name.drop_duplicates(subset=['gene']), right_on='gene', left_on='gene') 

        #marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/{species}/{marker_level}_markers_top1000.csv.gz', skiprows=1)
        #df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
        #marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
        #marker_list = marker_list[marker_list['gene_id'].isin(all_genes_spr)]
        marker_list = marker_list[marker_list['gene_id'].isin(tot_g)]
        #marker_list = marker_list[marker_list['rank'] < number_of_genes]
        all_cell_types = marker_list.drop_duplicates(['cell_type'])['cell_type'].tolist()
        df2_list = []
                    

                
        for group2 in all_cell_types:
                df2_list.append(marker_list[marker_list['cell_type']==group2].sort_values(by=['rank']).head(number_of_genes))

        marker_list=pd.concat(df2_list)

        marker_table = marker_list.pivot_table(index='gene_id', columns='cell_type', values='rank', aggfunc='sum')

        marker_table.fillna(0, inplace=True)
                    
        marker_table[marker_table != 0] = 1

        all_markers = marker_table.index.tolist()
                    


        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        marker_list_types = marker_list.drop_duplicates(subset=['cell_type'])['cell_type'].tolist()   
        marker_list_groups = marker_list.drop_duplicates(subset=['cell_type'])['group'].tolist()   
        df_list_mean = []

        cell_type_list_order = []
        
        df_list_p_val = []
        
        #all_cell_types  = ['Glutamatergic', 'GABAergic']

        for group, cell_type in zip(marker_list_groups, marker_list_types):

            
            
            
                    marker_genes_group = marker_table[marker_table[cell_type] == 1].index.tolist()

                    df_max_gene_whole_group_1 = df_max_gene_inter_by_bins.loc[marker_genes_group, :]

                    marker_genes_group = marker_table[marker_table[cell_type] != 1].index.tolist()

                    df_max_gene_whole_group_2 = df_max_gene_inter_by_bins.loc[marker_genes_group, :]

                    def addData(x):
                        try:
                            U, p_val = stats.ttest_ind(x.dropna().tolist(), df_max_gene_whole_group_2[x.name].dropna().tolist(), alternative="greater")
                            return p_val
                        except:
                            return np.nan


                    new_df = df_max_gene_whole_group_1.apply(addData)
                    df_list_p_val.append(new_df)
                    cell_type_list_order.append(cell_type)
                    column_list = df_max_gene_whole_group_1.columns.tolist()
                    j = new_df.to_numpy()
                    cell_type_name = cell_type.replace('/', "_")
                    outfile_name = f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/{marker_level}_{number_of_genes}_p_val_gene_nor_all_back_{cell_type}_vs_remaining_class_ttest.h5'

                    if os.path.isfile(outfile_name):
                        os.remove(outfile_name)

                    with h5py.File(outfile_name, 'a') as hf:



                        hf.create_dataset('type_contacts',data=j)
                        hf.create_dataset('type_list',data=cell_type)
                        hf.create_dataset('type_list_2',data='remaining')
                        hf.create_dataset('column_list',data=column_list)


                        
                        
number_of_genes_list = [1000]
marker_level_list = ['class']
#number_of_genes_list = [ 1000, 'opt', 10, 200]
#marker_level_list = ['class', 'subclass', 'cluster']
for number_of_genes in number_of_genes_list:
    for marker_level in marker_level_list:
        
        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/mouse_geneid_symbol.txt',sep='\t', names=['gene_id', 'gene'])
        #df_ensg_name['gene'] = df_ensg_name['gene'].str.upper()
        marker_list = marker_list.merge(df_ensg_name.drop_duplicates(subset=['gene']), right_on='gene', left_on='gene') 

        #marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/{species}/{marker_level}_markers_top1000.csv.gz', skiprows=1)
        #df_ensg_name = pd.read_csv('/grid/gillis/data/lohia/hi_c_data_processing/genomes_jlee/ensg_geneid_symbol.csv', sep='\t')[['Ensembl_gene_identifier', 'Symbol']]
        #marker_list = marker_list.merge(df_ensg_name.drop_duplicates(), right_on='Symbol', left_on='gene') 
        #marker_list = marker_list[marker_list['gene_id'].isin(all_genes_spr)]
        marker_list = marker_list[marker_list['gene_id'].isin(tot_g)]
        #marker_list = marker_list[marker_list['rank'] < number_of_genes]
        all_cell_types = marker_list.drop_duplicates(['cell_type'])['cell_type'].tolist()
        df2_list = []
                    

                
        for group2 in all_cell_types:
                df2_list.append(marker_list[marker_list['cell_type']==group2].sort_values(by=['rank']).head(number_of_genes))

        marker_list=pd.concat(df2_list)

        marker_table = marker_list.pivot_table(index='gene_id', columns='cell_type', values='rank', aggfunc='sum')

        marker_table.fillna(0, inplace=True)
                    
        marker_table[marker_table != 0] = 1

        all_markers = marker_table.index.tolist()
                    


        marker_list = pd.read_csv(f'/grid/gillis/data/lohia/hi_c_data_processing/notebooks/metamarkers/biccn_{marker_level}_markers.csv')
        marker_list_types = marker_list.drop_duplicates(subset=['cell_type'])['cell_type'].tolist()   
        marker_list_groups = marker_list.drop_duplicates(subset=['cell_type'])['group'].tolist()   
        df_list_mean = []

        cell_type_list_order = []
        
        df_list_p_val = []
        
        #all_cell_types  = ['Glutamatergic', 'GABAergic']

        for group, cell_type in zip(marker_list_groups, marker_list_types):
            for cell_type_2 in marker_list_types:
                
                if cell_type != cell_type_2:
            
            
            
                    marker_genes_group = marker_table[marker_table[cell_type] == 1].index.tolist()

                    df_max_gene_whole_group_1 = df_max_gene_inter_by_bins.loc[marker_genes_group, :]

                    marker_genes_group = marker_table[marker_table[cell_type_2] == 1].index.tolist()

                    df_max_gene_whole_group_2 = df_max_gene_inter_by_bins.loc[marker_genes_group, :]

                    def addData(x):
                        try:
                            U, p_val = stats.ttest_ind(x.dropna().tolist(), df_max_gene_whole_group_2[x.name].dropna().tolist(), alternative="greater")
                            return p_val
                        except:
                            return np.nan


                    new_df = df_max_gene_whole_group_1.apply(addData)
                    df_list_p_val.append(new_df)
                    cell_type_list_order.append(cell_type)
                    column_list = df_max_gene_whole_group_1.columns.tolist()
                    j = new_df.to_numpy()
                    cell_type_name = cell_type.replace('/', "_")
                    outfile_name = f'/grid/gillis/data/lohia/hi_c_data_processing/data_{species}/{SRP_name}/{resolution}/max/{marker_level}_{number_of_genes}_p_val_gene_nor_all_back_{cell_type}_vs_{cell_type_2}_class_ttest.h5'

                    if os.path.isfile(outfile_name):
                        os.remove(outfile_name)

                    with h5py.File(outfile_name, 'a') as hf:



                        hf.create_dataset('type_contacts',data=j)
                        hf.create_dataset('type_list',data=cell_type)
                        hf.create_dataset('type_list_2',data=cell_type_2)
                        hf.create_dataset('column_list',data=column_list)
                        
                        